周内效应分析番外——数字货币BTC篇

In [1]:
import pandas as pd
from datetime import datetime
import trdb2py
import numpy as np

isStaticImg = False
width = 960
height = 768

pd.options.display.max_columns = None
pd.options.display.max_rows = None

trdb2cfg = trdb2py.loadConfig('./trdb2.yaml')

In [20]:
# 具体基金
asset = 'bitmex.XBTUSD|1d'

# 起始时间，0表示从最开始算起
tsStart = 0
# tsStart = trdb2py.str2timestamp('2019-01-01', '%Y-%m-%d')

# 结束时间，-1表示到现在为止
tsEnd = -1
# tsEnd = trdb2py.str2timestamp('2020-01-01', '%Y-%m-%d')

# 初始资金池
paramsinit = trdb2py.trading2_pb2.InitParams(
    money=10000,
)

# 买入参数，用全部的钱来买入（也就是复利）
paramsbuy = trdb2py.trading2_pb2.BuyParams(
    perHandMoney=1,
)

# 卖出参数，全部卖出
paramssell = trdb2py.trading2_pb2.SellParams(
    perVolume=1,
)

大家好，我是格子衫小C，前面我们周内效应主要研究指数，其中成熟市场是没有明显的周内效应，今天来看看数字货币市场，看这种新兴市场是否有机会。

In [22]:
# baseline    
s0 = trdb2py.trading2_pb2.Strategy(
    name="normal",
    asset=trdb2py.str2asset(asset),         
)
        
buy0 = trdb2py.trading2_pb2.CtrlCondition(
    name='buyandhold',
)

paramsbuy = trdb2py.trading2_pb2.BuyParams(
    perHandMoney=1,
)

paramsinit = trdb2py.trading2_pb2.InitParams(
    money=10000,
)

s0.buy.extend([buy0])
s0.paramsBuy.CopyFrom(paramsbuy)
s0.paramsInit.CopyFrom(paramsinit)        
p0 = trdb2py.trading2_pb2.SimTradingParams(
    assets=[trdb2py.str2asset(asset)],
    startTs=tsStart,
    endTs=tsEnd,
    strategies=[s0],
    title='BTC',
)  

pnlBaseline = trdb2py.simTrading(trdb2cfg, p0)

trdb2py.showPNL(pnlBaseline, toImg=isStaticImg, width=width, height=height)

In [23]:
dfpnl1b = trdb2py.buildPNLReport([pnlBaseline])

dfpnl1b[['title', 'maxDrawdown', 'maxDrawdownStart', 'maxDrawdownEnd', 'totalReturns', 'sharpe', 'annualizedReturns', 'annualizedVolatility', 'variance']].sort_values(by='totalReturns', ascending=False)

title  maxDrawdown maxDrawdownStart maxDrawdownEnd  totalReturns     sharpe  \
0   BTC     0.837166       2017-12-17     2018-12-16    116.409439  27.251785   

   annualizedReturns  annualizedVolatility    variance  
0          21.905588              0.802721  402.415924

这是BTC近几年的数据，数据来源于BITMEX，BITMEX的指数是综合几家交易所的，相对更有代表性一些。

可以看到BTC从2015年到2020年12月，有116倍的回报率，而且最大回撤83%，真是惊心动魄的投资标的啊。

直接看看持有一天的情况。

In [24]:
lststart = [1, 2, 3, 4, 5, 6, 0]
lsttitle = ['周一', '周二', '周三', '周四', '周五', '周六', '周日']
lstparams = []

for i in range(0, 7):
    buy0 = trdb2py.trading2_pb2.CtrlCondition(
        name='weekday',
        vals=[lststart[i]],
    )

    sell0 = trdb2py.trading2_pb2.CtrlCondition(
        name='weekday',
        vals=[trdb2py.nextWeekDay(lststart[i], 1, 0, 6)],
    )

    s0 = trdb2py.trading2_pb2.Strategy(
        name="normal",
        asset=trdb2py.str2asset(asset),
    )

    s0.buy.extend([buy0])
    s0.sell.extend([sell0])
    s0.paramsBuy.CopyFrom(paramsbuy)
    s0.paramsSell.CopyFrom(paramssell)
    s0.paramsInit.CopyFrom(paramsinit)        
    lstparams.append(trdb2py.trading2_pb2.SimTradingParams(
        assets=[trdb2py.str2asset(asset)],
        startTs=tsStart,
        endTs=tsEnd,
        strategies=[s0],
        title='{}买入持有{}天'.format(lsttitle[i], 1),
    ))
 
lstpnl1 = trdb2py.simTradings(trdb2cfg, lstparams)

trdb2py.showPNLs(lstpnl1 + [pnlBaseline], toImg=isStaticImg, width=width, height=height)

In [25]:
dfpnl1b = trdb2py.buildPNLReport(lstpnl1 + [pnlBaseline])

dfpnl1b[['title', 'maxDrawdown', 'maxDrawdownStart', 'maxDrawdownEnd', 'totalReturns', 'sharpe', 'annualizedReturns', 'annualizedVolatility', 'variance']].sort_values(by='totalReturns', ascending=False)

title  maxDrawdown maxDrawdownStart maxDrawdownEnd  totalReturns  \
7       BTC     0.837166       2017-12-17     2018-12-16    116.409439   
0  周一买入持有1天     0.422177       2017-12-12     2018-12-17      5.940725   
5  周六买入持有1天     0.267107       2019-06-23     2020-04-04      3.431313   
4  周五买入持有1天     0.374935       2016-12-24     2017-07-28      2.426620   
2  周三买入持有1天     0.529212       2018-02-15     2018-11-21      1.921756   
1  周二买入持有1天     0.428421       2017-07-19     2020-01-07      1.371626   
3  周四买入持有1天     0.781295       2017-12-15     2020-03-19      1.022403   
6  周日买入持有1天     0.410071       2018-01-01     2020-08-16      0.873234   

      sharpe  annualizedReturns  annualizedVolatility    variance  
7  27.251785          21.905588              0.802721  402.415924  
0   3.114580           0.937787              0.291464    1.387684  
5   1.723969           0.461482              0.250284    0.499335  
4   0.810794           0.270783              0.296972    0.246005  
2   0.499006           0.174956              0.290490    0.056734  
1   0.137400           0.070537              0.295033    0.041359  
3  -0.059928           0.004252              0.429646    0.304715  
6  -0.232228          -0.024061              0.232793    0.013012

单独持有一天看起来都不太理想。

In [26]:
wrmt = trdb2py.buildPNLWinRateInYears(lstpnl1)

wrmt[0][['title', 'total']]

title     total
0  周一买入持有1天  0.523636
1  周二买入持有1天  0.534545
2  周三买入持有1天  0.547445
3  周四买入持有1天  0.540146
4  周五买入持有1天  0.576642
5  周六买入持有1天  0.610909
6  周日买入持有1天  0.523636

胜率上来看，周六买入的胜率最大（周六买入持有1天，就是以周六的close价格买入，周日close价格卖出，实际上是周日的上涨概率）。

下面看看每年的统计数据。

In [28]:
trdb2py.showBarWinRateInYears(lstpnl1, toImg=isStaticImg, width=width, height=height)

周六买入的胜率基本上每年都高于50%。

难道是因为周末BTC买入的人会变多？

In [29]:
trdb2py.showBarWinRate4Month(lstpnl1, toImg=isStaticImg, width=width, height=height)

这是按月统计得胜率数据，不过数据源其实就这么几年的，这个月数据统计意义不太大

In [30]:
lststart = [1, 2, 3, 4, 5, 6, 0]
lstval2 = [1, 1, 1, 1, 3]
lsttitle = ['周一', '周二', '周三', '周四', '周五', '周六', '周日']
lstparams = []

for day in range(1, 7):
    for i in range(0, 7):
        buy0 = trdb2py.trading2_pb2.CtrlCondition(
            name='weekday',
            vals=[lststart[i]],
        )

        sell0 = trdb2py.trading2_pb2.CtrlCondition(
            name='weekday',
            vals=[trdb2py.nextWeekDay(lststart[i], day, 0, 6)],
        )

        s0 = trdb2py.trading2_pb2.Strategy(
            name="normal",
            asset=trdb2py.str2asset(asset),
        )

        s0.buy.extend([buy0])
        s0.sell.extend([sell0])
        s0.paramsBuy.CopyFrom(paramsbuy)
        s0.paramsSell.CopyFrom(paramssell)
        s0.paramsInit.CopyFrom(paramsinit)        
        lstparams.append(trdb2py.trading2_pb2.SimTradingParams(
            assets=[trdb2py.str2asset(asset)],
            startTs=tsStart,
            endTs=tsEnd,
            strategies=[s0],
            title='{}买入持有{}天v2'.format(lsttitle[i], day),
        ))
 
lstpnl = trdb2py.simTradings(trdb2cfg, lstparams)

trdb2py.showPNLs(lstpnl + [pnlBaseline], toImg=isStaticImg, width=width, height=height)

In [31]:
dfpnl = trdb2py.buildPNLReport(lstpnl + [pnlBaseline])

dfpnl[['title', 'maxDrawdown', 'maxDrawdownStart', 'maxDrawdownEnd', 'totalReturns', 'sharpe', 'annualizedReturns', 'annualizedVolatility', 'variance']].sort_values(by='totalReturns', ascending=False)

title  maxDrawdown maxDrawdownStart maxDrawdownEnd  totalReturns  \
35  周一买入持有6天v2     0.808808       2017-12-17     2018-12-17    133.700668   
42         BTC     0.837166       2017-12-17     2018-12-16    116.409439   
39  周五买入持有6天v2     0.755914       2017-12-17     2018-12-12    113.208824   
37  周三买入持有6天v2     0.802448       2017-12-17     2018-12-16     83.148018   
38  周四买入持有6天v2     0.727020       2017-12-17     2018-12-16     60.114468   
32  周五买入持有5天v2     0.609084       2018-01-07     2018-12-16     58.797211   
40  周六买入持有6天v2     0.891444       2017-12-17     2020-03-17     47.971851   
33  周六买入持有5天v2     0.740284       2017-12-17     2018-11-27     46.920670   
31  周四买入持有5天v2     0.668818       2017-12-17     2018-12-16     43.266697   
25  周五买入持有4天v2     0.502223       2017-12-17     2018-12-16     42.318619   
28  周一买入持有5天v2     0.833546       2017-12-16     2018-12-17     38.850563   
41  周日买入持有6天v2     0.858235       2017-12-16     2018-12-16     33.925625   
26  周六买入持有4天v2     0.570958       2018-01-07     2018-12-04     24.415524   
29  周二买入持有5天v2     0.709819       2018-02-21     2019-01-16     22.505785   
36  周二买入持有6天v2     0.740519       2017-12-08     2020-03-13     19.755587   
19  周六买入持有3天v2     0.478825       2017-12-24     2018-02-12     17.800423   
23  周三买入持有4天v2     0.689654       2018-02-18     2020-03-13     16.408106   
21  周一买入持有4天v2     0.893543       2017-12-13     2020-03-17     16.010157   
14  周一买入持有3天v2     0.735985       2017-12-13     2018-12-12     15.659334   
30  周三买入持有5天v2     0.693863       2017-12-08     2020-03-13     14.403042   
34  周日买入持有5天v2     0.909408       2017-12-13     2020-03-17     13.980609   
27  周日买入持有4天v2     0.781909       2018-01-04     2018-11-21     13.674261   
17  周四买入持有3天v2     0.559393       2018-05-06     2020-03-13      8.538082   
11  周五买入持有2天v2     0.374068       2016-12-24     2017-07-22      8.350991   
7   周一买入持有2天v2     0.561543       2018-01-03     2018-12-17      8.148453   
24  周四买入持有4天v2     0.604864       2019-06-24     2020-03-13      7.494731   
18  周五买入持有3天v2     0.378926       2020-03-14     2020-06-28      7.330503   
20  周日买入持有3天v2     0.643390       2018-01-03     2018-12-04      7.115504   
22  周二买入持有4天v2     0.754428       2017-12-08     2020-03-13      6.539701   
0   周一买入持有1天v2     0.422177       2017-12-12     2018-12-17      5.940725   
13  周日买入持有2天v2     0.528863       2018-01-01     2018-02-12      5.187642   
16  周三买入持有3天v2     0.710272       2017-12-08     2020-03-13      4.767845   
5   周六买入持有1天v2     0.267107       2019-06-23     2020-04-04      3.431313   
12  周六买入持有2天v2     0.467509       2019-06-24     2020-06-28      2.996338   
15  周二买入持有3天v2     0.868123       2017-12-13     2020-03-17      2.694984   
8   周二买入持有2天v2     0.598239       2018-01-11     2018-11-21      2.635930   
10  周四买入持有2天v2     0.595087       2017-12-16     2020-03-13      2.480984   
4   周五买入持有1天v2     0.374935       2016-12-24     2017-07-28      2.426620   
9   周三买入持有2天v2     0.842335       2017-12-08     2020-03-18      1.964809   
2   周三买入持有1天v2     0.529212       2018-02-15     2018-11-21      1.921756   
1   周二买入持有1天v2     0.428421       2017-07-19     2020-01-07      1.371626   
3   周四买入持有1天v2     0.781295       2017-12-15     2020-03-19      1.022403   
6   周日买入持有1天v2     0.410071       2018-01-01     2020-08-16      0.873234   

       sharpe  annualizedReturns  annualizedVolatility    variance  
35  32.751480          25.187593              0.768136  467.224884  
42  27.251785          21.905588              0.802721  402.415924  
39  31.371843          21.298088              0.677936  359.616394  
37  20.843536          15.592318              0.746626  220.496567  
38  14.949511          11.220375              0.748545  170.442032  
32  17.847889          10.970349              0.612977  130.750839  
40  11.907469           8.915614              0.746222  148.563156  
33  14.236277           8.716092              0.610138   65.505112  